# Parallel demand forecasting at scale using Ray Tune and Pyspark UDF

Batch training and tuning are common tasks in machine learning use-cases. They require training simple models, on data batches, typcially corresponding to different locations, products, etc. Batch training can take less time to process all the data at once, but only if those batches can run in parallel!

This notebook showcases how to conduct batch forecasting with NeuralProphet. NeuralProphet is a popular open-source library developed by Facebook and designed for automatic forecasting of univariate time series data. 
<br></br>
<div style="text-align: center; line-height: 5; padding-top: 20px;  padding-bottom: 20px;">
  <img src="https://docs.ray.io/en/master/_images/batch-training.svg" alt='Push compute' height="300" width="400">
</div>

For the data, we will use the M5 walmart dataset.This popular tabular dataset contains historical sales of products for different locations and regions in USA

### Import the libraries

In [0]:
import random
import multiprocessing
import numpy as np
from datetime import timedelta, date
import traceback
import math
import timeit
import torch
import mlflow
from mlflow.tracking import MlflowClient

import pandas as pd
import neuralprophet
from neuralprophet import NeuralProphet, set_log_level


# importing hyperopt and ray
from hyperopt import hp
import ray
from ray import tune
from ray.tune.schedulers import AsyncHyperBandScheduler
from ray.tune.search.hyperopt import HyperOptSearch
from ray.tune.stopper import TimeoutStopper
from ray.tune.search.concurrency_limiter import ConcurrencyLimiter
from ray.runtime_env import RuntimeEnv

from hyperopt.pyll import scope
from itertools import product
from ray.util.multiprocessing import Pool

import multiprocessing
num_cpus = multiprocessing.cpu_count()
print(num_cpus)

import logging

from delta.tables import DeltaTable
#from pyspark.sql.functions import col, min, max, sum, abs, mean, when, lit, date_format,desc,asc, dense_rank, avg, pow, sqrt
from pyspark.sql import Window
from sklearn.metrics import mean_squared_error
from datetime import datetime
import json
import time, os
from ast import literal_eval
from pytorch_lightning.callbacks.early_stopping import EarlyStopping
import pyspark.sql.functions as F

/databricks/python/lib/python3.9/site-packages/pkg_resources/__init__.py:122: PkgResourcesDeprecationWarning: 0.23ubuntu1 is an invalid version and will not be supported in a future release
  warnings.warn(
/databricks/python/lib/python3.9/site-packages/pkg_resources/__init__.py:122: PkgResourcesDeprecationWarning: 0.23ubuntu1 is an invalid version and will not be supported in a future release
  warnings.warn(


8


## Ray Cluster Setup :

There are 2 options of settig up ray cluster on databricks:
- **Using the setup_ray_cluster API**
  ```
    setup_ray_cluster(
      num_worker_nodes=MAX_NUM_WORKER_NODES,
      num_cpus_per_node=int(num_cpu_cores_per_worker),
      num_gpus_per_node=int(num_gpu_per_worker),
      collect_log_to_path=RAY_LOG_DIR #ray_collected_logs
      )

    ray.init(address='auto')

    num_workers = (ray.cluster_resources()["CPU"]/num_cpu_cores_per_worker)
  ```
- **Using init scripts**
  ```
  #!/bin/bash
  #RAY PORT
  RAY_PORT=9339
  REDIS_PASS="d4t4bricks"

  # install ray
  # Install additional ray libraries
  /databricks/python/bin/pip install ray[tune]==2.5.1
  /databricks/python/bin/pip install ray[default]==2.5.1
  /databricks/python/bin/pip install ray[rllib]==2.5.1
  /databricks/python/bin/pip install prophet==1.1.1
  /databricks/python/bin/pip install "holidays==0.11.3.1" --force-reinstall

  mkdir /tmp/ray/job

  # If starting on the Spark driver node, initialize the Ray head node
  # If starting on the Spark worker node, connect to the head Ray node
  if [ ! -z $DB_IS_DRIVER ] && [ $DB_IS_DRIVER = TRUE ] ; then
    echo "Starting the head node"
    ulimit -n 1000000
    ray start  --head --min-worker-port=20000 --max-worker-port=25000 --temp-dir="/tmp/ray/job" --plasma-directory="/tmp/ray/job" --port=$RAY_PORT --dashboard-port=8501 --dashboard-host="0.0.0.0" --include-dashboard=true --num-cpus=0
  else
    sleep 40
    ulimit -n 1000000
    echo "Starting the non-head node - connecting to $DB_DRIVER_IP:$RAY_PORT"
    ray start  --min-worker-port=20000 --max-worker-port=25000 --temp-dir="/tmp/ray/job" --plasma-directory="/tmp/ray/job" --address="$DB_DRIVER_IP:$RAY_PORT"  
  fi
  ```

## Visualize the ray dashboard

In [0]:
%run ./ray_dashboard

Once the dashbord is running, it can be accessed at this link:

https://adb-7395199854110807.7.azuredatabricks.net/driver-proxy/o/7395199854110807/0509-092114-2vh26ow5/8501/


Open Link to the Ray Dashboard in a new tab

In [0]:
ray.init('auto', ignore_reinit_error=True)
ray_resources = ray.cluster_resources()
# ray.shutdown()

2023-06-27 00:27:13,521	INFO worker.py:1432 -- Connecting to existing Ray cluster at address: 10.150.84.10:9339...
2023-06-27 00:27:13,529	INFO worker.py:1616 -- Connected to Ray cluster. View the dashboard at 10.150.84.10:8501 


# Reading walmart data

In [0]:
sdf_walmart = spark.read.format('parquet').load('dbfs:/mnt/enterprise/dataaisummit/m5_clean_data/final_cleaned_table/')

In [0]:
display(sdf_walmart)

item_id dept_id cat_id store_id state_id date_time sell_price sale_quantity FOODS_1_002 FOODS_1 FOODS CA_4 CA 2011-01-29 7.88 0 FOODS_1_002 FOODS_1 FOODS CA_4 CA 2011-01-30 7.88 1 FOODS_1_002 FOODS_1 FOODS CA_4 CA 2011-01-31 7.88 2 FOODS_1_002 FOODS_1 FOODS CA_4 CA 2011-02-01 7.88 1 FOODS_1_002 FOODS_1 FOODS CA_4 CA 2011-02-02 7.88 0 FOODS_1_002 FOODS_1 FOODS CA_4 CA 2011-02-03 7.88 0 FOODS_1_002 FOODS_1 FOODS CA_4 CA 2011-02-04 7.88 0 FOODS_1_004 FOODS_1 FOODS CA_4 CA 2011-01-29 null 0 FOODS_1_004 FOODS_1 FOODS CA_4 CA 2011-01-30 null 0 FOODS_1_004 FOODS_1 FOODS CA_4 CA 2011-01-31 null 0 FOODS_1_004 FOODS_1 FOODS CA_4 CA 2011-02-01 null 0 FOODS_1_004 FOODS_1 FOODS CA_4 CA 2011-02-02 null 0 FOODS_1_004 FOODS_1 FOODS CA_4 CA 2011-02-03 null 0 FOODS_1_004 FOODS_1 FOODS CA_4 CA 2011-02-04 null 0 FOODS_1_006 FOODS_1 FOODS WI_1 WI 2011-01-29 1.97 3 FOODS_1_006 FOODS_1 FOODS WI_1 WI 2011-01-30 1.97 3 FOODS_1_006 FOODS_1 FOODS WI_1 WI 2011-01-31 1.97 5 FOODS_1_006 FOODS_1 FOODS WI_1 WI 2011-02-01 1.97 0 FOODS_1_006 FOODS_1 FOODS WI_1 WI 2011-02-02 1.97 0 FOODS_1_006 FOODS_1 FOODS WI_1 WI 2011-02-03 1.97 1 FOODS_1_006 FOODS_1 FOODS WI_1 WI 2011-02-04 1.97 14 FOODS_1_009 FOODS_1 FOODS WI_1 WI 2011-01-29 null 0 FOODS_1_009 FOODS_1 FOODS WI_1 WI 2011-01-30 null 0 FOODS_1_009 FOODS_1 FOODS WI_1 WI 2011-01-31 null 0 FOODS_1_009 FOODS_1 FOODS WI_1 WI 2011-02-01 null 0 FOODS_1_009 FOODS_1 FOODS WI_1 WI 2011-02-02 null 0 FOODS_1_009 FOODS_1 FOODS WI_1 WI 2011-02-03 null 0 FOODS_1_009 FOODS_1 FOODS WI_1 WI 2011-02-04 null 0 FOODS_1_011 FOODS_1 FOODS WI_1 WI 2011-01-29 null 0 FOODS_1_011 FOODS_1 FOODS WI_1 WI 2011-01-30 null 0 FOODS_1_011 FOODS_1 FOODS WI_1 WI 2011-01-31 null 0 FOODS_1_011 FOODS_1 FOODS WI_1 WI 2011-02-01 null 0 FOODS_1_011 FOODS_1 FOODS WI_1 WI 2011-02-02 null 0 FOODS_1_011 FOODS_1 FOODS WI_1 WI 2011-02-03 null 0 FOODS_1_011 FOODS_1 FOODS WI_1 WI 2011-02-04 null 0 FOODS_1_012 FOODS_1 FOODS TX_3 TX 2011-01-29 null 0 FOODS_1_012 FOODS_1 FOODS TX_3 TX 2011-01-30 null 0 FOODS_1_012 FOODS_1 FOODS TX_3 TX 2011-01-31 null 0 FOODS_1_012 FOODS_1 FOODS TX_3 TX 2011-02-01 null 0 FOODS_1_012 FOODS_1 FOODS TX_3 TX 2011-02-02 null 0 FOODS_1_012 FOODS_1 FOODS TX_3 TX 2011-02-03 null 0 FOODS_1_012 FOODS_1 FOODS TX_3 TX 2011-02-04 null 0 FOODS_1_015 FOODS_1 FOODS CA_2 CA 2011-01-29 null 0 FOODS_1_015 FOODS_1 FOODS CA_2 CA 2011-01-30 null 0 FOODS_1_015 FOODS_1 FOODS CA_2 CA 2011-01-31 null 0 FOODS_1_015 FOODS_1 FOODS CA_2 CA 2011-02-01 null 0 FOODS_1_015 FOODS_1 FOODS CA_2 CA 2011-02-02 null 0 FOODS_1_015 FOODS_1 FOODS CA_2 CA 2011-02-03 null 0 FOODS_1_015 FOODS_1 FOODS CA_2 CA 2011-02-04 null 0 FOODS_1_016 FOODS_1 FOODS WI_3 WI 2011-01-29 1.96 4 FOODS_1_016 FOODS_1 FOODS WI_3 WI 2011-01-30 1.96 0 FOODS_1_016 FOODS_1 FOODS WI_3 WI 2011-01-31 1.96 0 FOODS_1_016 FOODS_1 FOODS WI_3 WI 2011-02-01 1.96 0 FOODS_1_016 FOODS_1 FOODS WI_3 WI 2011-02-02 1.96 0 FOODS_1_016 FOODS_1 FOODS WI_3 WI 2011-02-03 1.96 1 FOODS_1_016 FOODS_1 FOODS WI_3 WI 2011-02-04 1.96 0 FOODS_1_018 FOODS_1 FOODS CA_1 CA 2011-01-29 1.0 17 FOODS_1_018 FOODS_1 FOODS CA_1 CA 2011-01-30 1.0 3 FOODS_1_018 FOODS_1 FOODS CA_1 CA 2011-01-31 1.0 8 FOODS_1_018 FOODS_1 FOODS CA_1 CA 2011-02-01 1.0 2 FOODS_1_018 FOODS_1 FOODS CA_1 CA 2011-02-02 1.0 5 FOODS_1_018 FOODS_1 FOODS CA_1 CA 2011-02-03 1.0 0 FOODS_1_018 FOODS_1 FOODS CA_1 CA 2011-02-04 1.0 1 FOODS_1_018 FOODS_1 FOODS TX_1 TX 2011-01-29 0.92 0 FOODS_1_018 FOODS_1 FOODS TX_1 TX 2011-01-30 0.92 1 FOODS_1_018 FOODS_1 FOODS TX_1 TX 2011-01-31 0.92 0 FOODS_1_018 FOODS_1 FOODS TX_1 TX 2011-02-01 0.92 0 FOODS_1_018 FOODS_1 FOODS TX_1 TX 2011-02-02 0.92 1 FOODS_1_018 FOODS_1 FOODS TX_1 TX 2011-02-03 0.92 1 FOODS_1_018 FOODS_1 FOODS TX_1 TX 2011-02-04 0.92 1 FOODS_1_018 FOODS_1 FOODS TX_3 TX 2011-01-29 0.92 5 FOODS_1_018 FOODS_1 FOODS TX_3 TX 2011-01-30 0.92 1 FOODS_1_018 FOODS_1 FOODS TX_3 TX 2011-01-31 0.92 8 FOODS_1_018 FOODS_1 FOODS TX_3 TX 2011-02-01 0.92 1 FOODS_1_018 FOODS_1 FOODS TX_3 TX 2011-02-02 0.92 0 FOODS_1_018 FOODS_1 FOODS TX_

## Get The cluster information

In [0]:
import requests
ctx = dbutils.notebook.entry_point.getDbutils().notebook().getContext()
host_name = ctx.tags().get("browserHostName").get()
host_token = ctx.apiToken().get()
cluster_id = ctx.tags().get("clusterId").get()

response = requests.get(
    f'https://{host_name}/api/2.0/clusters/get?cluster_id={cluster_id}',
    headers={'Authorization': f'Bearer {host_token}'}
  ).json()
cluster_info = {
  'driver_type': response['driver_node_type_id'],
  'worker_type': response['node_type_id'],
  'num_workers': response['num_workers'],
  'spark_ver': response['spark_version'],
  'cluster_memory_mb': response['cluster_memory_mb']
}
cluster_info=json.dumps(cluster_info)
print(cluster_info)

{"driver_type": "Standard_NC8as_T4_v3", "worker_type": "Standard_NC8as_T4_v3", "num_workers": 2, "spark_ver": "12.2.x-gpu-ml-scala2.12", "cluster_memory_mb": 172032}


### Create Random time-series per model for the Demo.
make sure num_items and items_per_model are divisible

In [0]:
# Experiment setup - make sure num_items and items_per_model are divisible
num_items = 200  # Max number of item time series to load, full dataset has 30490 which is overkill
items_per_model = 100  # Number of item time series per model
num_batches = 1  # num trials = max_concurrent_trials * num_batches

In [0]:

window_spec = Window.orderBy('state_id', 'store_id', 'cat_id', 'dept_id', 'item_id')
sdf_walmart_with_model_num = sdf_walmart.withColumn("item_num", F.dense_rank().over(window_spec))  # A unique item number based on the window
sdf_walmart_with_model_num = sdf_walmart_with_model_num.filter(sdf_walmart_with_model_num.item_num <= num_items)
sdf_walmart_with_model_num = sdf_walmart_with_model_num.withColumn("model_num", F.ceil(F.col("item_num") / items_per_model))
sdf_walmart_with_model_num = sdf_walmart_with_model_num.withColumn('y', F.col('sell_price')*F.col('sale_quantity'))
sdf_walmart_with_model_num.cache()
print(sdf_walmart.count())
sdf_walmart_with_model_num.display()

59181090


item_id dept_id cat_id store_id state_id date_time sell_price sale_quantity item_num model_num y FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-06-04 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-06-05 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-06-06 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-06-07 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-06-08 2.0 1 1 1 2.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-06-09 2.0 4 1 1 8.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-06-10 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-09-10 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-09-11 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-09-12 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-09-13 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-09-14 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-09-15 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-09-16 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-11-05 2.0 2 1 1 4.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-11-06 2.0 1 1 1 2.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-11-07 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-11-08 2.0 2 1 1 4.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-11-09 2.0 1 1 1 2.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-11-10 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2011-11-11 2.0 1 1 1 2.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-08-18 2.0 4 1 1 8.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-08-19 2.0 2 1 1 4.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-08-20 2.0 6 1 1 12.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-08-21 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-08-22 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-08-23 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-08-24 2.0 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-09-01 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-09-02 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-09-03 2.24 2 1 1 4.48 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-09-04 2.24 2 1 1 4.48 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-09-05 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-09-06 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-09-07 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-10-20 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-10-21 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-10-22 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-10-23 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-10-24 2.24 3 1 1 6.720000000000001 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-10-25 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-10-26 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-12-29 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-12-30 2.24 2 1 1 4.48 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2012-12-31 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-01-01 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-01-02 2.24 2 1 1 4.48 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-01-03 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-01-04 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-03-02 2.24 2 1 1 4.48 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-03-03 2.24 2 1 1 4.48 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-03-04 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-03-05 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-03-06 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-03-07 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-03-08 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-04-20 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-04-21 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-04-22 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-04-23 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-04-24 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-04-25 2.24 0 1 1 0.0 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-04-26 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-05-25 2.24 1 1 1 2.24 FOODS_1_001 FOODS_1 FOODS CA_1 CA 2013-05-26 2.24 0 1 1

# Many model Forecasting with Ray Tune and Pyspark UDF
Ray Tune is a powerful library for hyperparameter tuning, designed to simplify the development of distributed applications. It allows you to efficiently sample hyperparameters and get optimized results on your objective function. Ray Tune provides a variety of state-of-the-art hyperparameter tuning algorithms for optimizing model performance. 

To use Ray Tune for hyperparameter tuning, you can follow these steps:
- Define your training function and objective function.
- Specify the hyperparameters and their search space.
- Define the pyspark udf function which runs ray tune for each Hierarchial model for the chosen search algorithm and scheduler.
- Run the pyspark job and get the result

## Step 1 : Define the training and objective function

In [0]:
def ray_trial(config, df):
  """
  Single ray trial of parameter config 
  This runs a NeuralProphet model based on the given config and then loads  
  """
  test_cutoff = df['ds'].max() - pd.Timedelta(days=7)
  df_train = df[df['ds'] < test_cutoff]
  df_test = df
  trainer_config = {}
  # Define the Model (it can be any model in our case we use NeuralProphet)
  model = NeuralProphet(
      accelerator='auto',
      trainer_config=trainer_config,
      **config
  )
  start = timeit.default_timer()
  # Train model
  model.fit(
    df=df_train,
    freq="D",
    metrics=['RMSE'],
    progress='bar'
  )
  total_time = timeit.default_timer()-start
  print("duration of model fit: ", total_time)
  print(f"df length: {df_test.shape}")
  # Validate the model and get the RMSE Score
  forecast_week = model.predict(df[df['ds'] >= test_cutoff])
  forecast_week.y.fillna(0, inplace=True)
  forecast_week.yhat1.fillna(0, inplace=True)
  test_rmse = mean_squared_error(forecast_week.yhat1.tolist(), forecast_week.y.tolist(), squared=False)
  tune.report(RMSE=test_rmse, checkpoint = model)

## Step 2 : Define the search space

In [0]:
space_str = """
{
  "learning_rate": tune.uniform(0.001, 1),
  "n_changepoints": 10,
  "n_lags": 3, 
  'drop_missing': True,
  'impute_rolling': 300,
  'newer_samples_weight': tune.uniform(1, 7),
  'batch_size': 128,
  "ar_layers": tune.choice([[64,64,64],[128,128,128],[256,256,256]]),
  'epochs': 10
}
"""

## Step 3 : Define the pyspark udf function which runs ray tune for each Hierarchial model for the chosen search algorithm and scheduler.

In [0]:
def udf_parallel_hpt_tune(keys, df):
  """
  Single ray trial of parameter config 
  This runs a NeuralProphet model based on the given config and then loads  
  """
  start = timeit.default_timer()
  model_num = keys[0]
  df['date_time'] = pd.to_datetime(df['date_time'], format='%Y-%m-%d')
  df = df.sort_values(by='date_time', ascending=True)
  df = df.rename(columns={'date_time': 'ds', 'item_num': 'ID'})
  df = df[['ID', 'ds', 'y']]
  space = eval(space_str)
  ray.init(
    address="auto",
    ignore_reinit_error=True,
    include_dashboard=False,
    log_to_driver=True,
  )
  tune_resources = {"CPU": cpu_resources_per_trial} if \
                     gpu_resources_per_trial == 0 else \
                      {"CPU": cpu_resources_per_trial,\
                                     "GPU": gpu_resources_per_trial}
  algo = HyperOptSearch(
    space,
    metric='RMSE',
    mode="min",
  )
  scheduler = AsyncHyperBandScheduler()
  analysis = tune.run(
    tune.with_parameters(ray_trial, df=df),
    search_alg=algo,
    scheduler=scheduler,
    metric="RMSE",
    mode="min",
    max_concurrent_trials=max_concurrent_trials,
    num_samples=max_concurrent_trials * num_batches,
    reuse_actors=True,
    resources_per_trial=tune.PlacementGroupFactory(
      [tune_resources],
      strategy="PACK"
    ),
  )
  best_trial = analysis.get_best_trial(scope='last-5-avg')
  print(f'aaa:{best_trial.last_result["config"]}')
  current_experiment=dict(mlflow.get_experiment_by_name(experiment_location))
  experiment_id=current_experiment['experiment_id']
  client = MlflowClient()
  child_run = client.create_run(experiment_id = experiment_id,
                                run_name=f"model_{str(model_num)}",
                                tags={"mlflow.parentRunId": run_id})
  for key ,value in best_trial.last_result['config'].items():
    client.log_param( run_id=child_run.info.run_id,
                      key = key,
                      value = str(value))
  client.log_metric( run_id=child_run.info.run_id,key = 'rmse', value = best_trial.last_result['RMSE'])
    # with mlflow.start_run(run_name=f"model_{str(model_num)}" , nested=True):
    #   mlflow.log_metric(key = 'rmse', value = best_trial.last_result['RMSE'])
  print(f'aaa:{best_trial.last_result}')
  best_rmse = best_trial.last_result['RMSE']
  return pd.DataFrame([{
    'model_num': model_num,
    'model_HPT_time': str(timeit.default_timer()-start), 
    'num_datapoints': df['y'].count(),
    'RMSE': best_rmse,
    'space': space_str
    }])



When using pyspark udf we have to define the schema of the output generated by the udf

In [0]:
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, IntegerType

results_schema = StructType([
  # StructField('state_id', StringType(), True),
  # StructField('store_id', StringType(), True),
  # StructField('cat_id', StringType(), True),
  # StructField('dept_id', StringType(), True),
  StructField('model_num', IntegerType(), True),
  StructField('model_HPT_time', StringType(), True),
  StructField('num_datapoints', IntegerType(), True),
  StructField('RMSE', DoubleType(), True),
  StructField('space', StringType(), True),
])

## Step 4 : Run the pyspark job and get the results.

Here we dynamically specify the resources to be used based on the cluster choosen betweem CPU and GPU

In [0]:
max_concurrent_trials = 1
num_models = sdf_walmart_with_model_num.select(F.max('model_num')).collect()[0][0]
print(f"num models : {num_models}")
total_concurrent_trials = num_models*max_concurrent_trials
print(f"Total concurrent Trials: {total_concurrent_trials}")
gpu_resources_per_trial = ray_resources['GPU']/total_concurrent_trials if 'GPU' in ray_resources.keys() else 0
cpu_resources_per_trial = min(int(math.ceil((ray_resources['CPU']/num_models)/max_concurrent_trials)),16)
print(f'gpu_resources_per_trial:{gpu_resources_per_trial}\ncpu_resources_per_trial:{cpu_resources_per_trial}')
print(f"***Creating DF to ray tune on {num_models} models with {items_per_model} item time seies per model***")
# sdf_walmart_with_model_num.groupBy('state_id', 'store_id', 'cat_id', 'dept_id', 'item_id').agg(F.first('item_num').alias('item_num'), F.first('model_num').alias('model_num')).display()

num models : 2
Total concurrent Trials: 2
gpu_resources_per_trial:1.0
cpu_resources_per_trial:8
***Creating DF to ray tune on 2 models with 100 item time seies per model***


In [0]:
sdf_walmart_with_model_set = sdf_walmart_with_model_num.select('model_num','store_id','item_id'). \
                                      groupBy('model_num').agg(F.collect_set('store_id').alias('store_id'),
                                      F.collect_set('item_id').alias('item_id'), ).display()

model_num store_id item_id 1 List(CA_1) List(FOODS_1_050, FOODS_1_034, FOODS_1_009, FOODS_1_096, FOODS_1_095, FOODS_1_073, FOODS_1_033, FOODS_1_054, FOODS_1_005, FOODS_1_037, FOODS_1_038, FOODS_1_002, FOODS_1_065, FOODS_1_035, FOODS_1_052, FOODS_1_025, FOODS_1_048, FOODS_1_078, FOODS_1_080, FOODS_1_085, FOODS_1_019, FOODS_1_077, FOODS_1_060, FOODS_1_058, FOODS_1_011, FOODS_1_015, FOODS_1_003, FOODS_1_071, FOODS_1_041, FOODS_1_081, FOODS_1_036, FOODS_1_044, FOODS_1_084, FOODS_1_102, FOODS_1_012, FOODS_1_017, FOODS_1_021, FOODS_1_001, FOODS_1_026, FOODS_1_091, FOODS_1_063, FOODS_1_092, FOODS_1_051, FOODS_1_023, FOODS_1_089, FOODS_1_020, FOODS_1_030, FOODS_1_098, FOODS_1_101, FOODS_1_014, FOODS_1_049, FOODS_1_053, FOODS_1_004, FOODS_1_086, FOODS_1_039, FOODS_1_062, FOODS_1_067, FOODS_1_031, FOODS_1_099, FOODS_1_075, FOODS_1_079, FOODS_1_083, FOODS_1_045, FOODS_1_042, FOODS_1_032, FOODS_1_074, FOODS_1_082, FOODS_1_087, FOODS_1_064, FOODS_1_068, FOODS_1_094, FOODS_1_056, FOODS_1_076, FOODS_1_027, FOODS_1_029, FOODS_1_043, FOODS_1_069, FOODS_1_061, FOODS_1_057, FOODS_1_066, FOODS_1_040, FOODS_1_016, FOODS_1_013, FOODS_1_028, FOODS_1_006, FOODS_1_055, FOODS_1_024, FOODS_1_072, FOODS_1_090, FOODS_1_093, FOODS_1_008, FOODS_1_018, FOODS_1_070, FOODS_1_046, FOODS_1_022, FOODS_1_088, FOODS_1_059, FOODS_1_047, FOODS_1_097, FOODS_1_010) 2 List(CA_1) List(FOODS_1_193, FOODS_1_197, FOODS_1_116, FOODS_1_119, FOODS_1_173, FOODS_1_150, FOODS_1_104, FOODS_1_198, FOODS_1_130, FOODS_1_168, FOODS_1_163, FOODS_1_158, FOODS_1_176, FOODS_1_191, FOODS_1_129, FOODS_1_184, FOODS_1_171, FOODS_1_175, FOODS_1_194, FOODS_1_118, FOODS_1_166, FOODS_1_125, FOODS_1_177, FOODS_1_143, FOODS_1_187, FOODS_1_137, FOODS_1_131, FOODS_1_114, FOODS_1_103, FOODS_1_115, FOODS_1_155, FOODS_1_185, FOODS_1_126, FOODS_1_108, FOODS_1_140, FOODS_1_147, FOODS_1_164, FOODS_1_128, FOODS_1_106, FOODS_1_141, FOODS_1_145, FOODS_1_153, FOODS_1_188, FOODS_1_159, FOODS_1_192, FOODS_1_123, FOODS_1_181, FOODS_1_183, FOODS_1_199, FOODS_1_134, FOODS_1_156, FOODS_1_162, FOODS_1_111, FOODS_1_203, FOODS_1_138, FOODS_1_167, FOODS_1_186, FOODS_1_178, FOODS_1_124, FOODS_1_121, FOODS_1_144, FOODS_1_189, FOODS_1_202, FOODS_1_149, FOODS_1_107, FOODS_1_122, FOODS_1_196, FOODS_1_136, FOODS_1_127, FOODS_1_142, FOODS_1_139, FOODS_1_113, FOODS_1_151, FOODS_1_174, FOODS_1_112, FOODS_1_160, FOODS_1_117, FOODS_1_154, FOODS_1_201, FOODS_1_109, FOODS_1_169, FOODS_1_179, FOODS_1_161, FOODS_1_170, FOODS_1_120, FOODS_1_172, FOODS_1_146, FOODS_1_152, FOODS_1_132, FOODS_1_133, FOODS_1_200, FOODS_1_182, FOODS_1_180, FOODS_1_135, FOODS_1_190, FOODS_1_148, FOODS_1_195, FOODS_1_110, FOODS_1_105, FOODS_1_157)

In [0]:
spark.conf.set('spark.sql.adaptive.coalescePartitions.enabled', 'false')
spark.conf.set('spark.sql.adaptive.enabled', 'false')
spark.conf.set('spark.databricks.optimizer.adaptive.enabled', 'false')
spark.conf.set('spark.sql.shuffle.partitions', f'{num_models}')
num_models

Out[17]: 2

In [0]:
experiment_location =  '/Users/puneet.jain@mnscorp.net/Dais_many_model_forecasting_demo'
experiment_name = 'hpt'

In [0]:
get_or_create_experiment(experiment_location)
run_id = get_new_run(experiment_location, experiment_name+"_"+str(date.today()))

In [0]:
start = timeit.default_timer()
with mlflow.start_run(run_id=run_id):
  results = sdf_walmart_with_model_num.repartition(num_models).\
            groupBy(['model_num']).applyInPandas(func=udf_parallel_hpt_tune, schema=results_schema)
display(results.toPandas())
total_time = timeit.default_timer()-start
print("duration of execution: ", total_time)

model_num model_HPT_time num_datapoints RMSE space 2 106.74395973799994 160913 6.752816227323234 
{
 "learning_rate": tune.uniform(0.001, 1),
 "n_changepoints": 10,
 "n_lags": 3, 
 'drop_missing': True,
 'impute_rolling': 300,
 'newer_samples_weight': tune.uniform(1, 7),
 'batch_size': 128,
 "ar_layers": tune.choice([[64,64,64],[128,128,128],[256,256,256]]),
 'epochs': 10
}
 1 110.89095562900002 168711 16.790971167565026 
{
 "learning_rate": tune.uniform(0.001, 1),
 "n_changepoints": 10,
 "n_lags": 3, 
 'drop_missing': True,
 'impute_rolling': 300,
 'newer_samples_weight': tune.uniform(1, 7),
 'batch_size': 128,
 "ar_layers": tune.choice([[64,64,64],[128,128,128],[256,256,256]]),
 'epochs': 10
}

duration of execution:  119.70532675099992


We see for each trial the cluster utilizes on 25% of the computation
<br></br>
<div style="text-align: center; line-height: 5; padding-top: 20px;  padding-bottom: 20px;">
  <img src="https://raw.githubusercontent.com/puneet-jain159/Image_dump/test/ray_25_dash_utilization.png" alt='Push compute' height="1000" width="1600">
</div>

In [0]:
# Here we see that only 25% percent of the GPU is being utlized to when running the trails

# Improving the cluster utilization

Since we are consuming 25% let us increase the number of trails to 4 to utlize the GPU Cluster properly

In [0]:
max_concurrent_trials = 4
num_models = sdf_walmart_with_model_num.select(F.max('model_num')).collect()[0][0]
print(f"num models : {num_models}")
total_concurrent_trials = num_models*max_concurrent_trials
print(f"Total concurrent Trials: {total_concurrent_trials}")
gpu_resources_per_trial = ray_resources['GPU']/total_concurrent_trials if 'GPU' in ray_resources.keys() else 0
cpu_resources_per_trial = min(int(math.ceil((ray_resources['CPU']/num_models)/max_concurrent_trials)),16)
print(f'gpu_resources_per_trial:{gpu_resources_per_trial}\ncpu_resources_per_trial:{cpu_resources_per_trial}')
print(f"***Creating DF to ray tune on {num_models} models with {items_per_model} item time seies per model***")

num models : 2
Total concurrent Trials: 8
gpu_resources_per_trial:0.25
cpu_resources_per_trial:2
***Creating DF to ray tune on 2 models with 100 item time seies per model***


In [0]:
run_id = get_new_run(experiment_location, experiment_name+"_"+str(date.today())+"_max_trials_" +str(max_concurrent_trials))

start = timeit.default_timer()
with mlflow.start_run(run_id=run_id):
  results = sdf_walmart_with_model_num.repartition(num_models).\
            groupBy(['model_num']).applyInPandas(func=udf_parallel_hpt_tune, schema=results_schema)
display(results.toPandas())
total_time = timeit.default_timer()-start
print("duration of execution: ", total_time)

model_num model_HPT_time num_datapoints RMSE space 2 134.20414228000004 160913 6.752816227323234 
{
 "learning_rate": tune.uniform(0.001, 1),
 "n_changepoints": 10,
 "n_lags": 3, 
 'drop_missing': True,
 'impute_rolling': 300,
 'newer_samples_weight': tune.uniform(1, 7),
 'batch_size': 128,
 "ar_layers": tune.choice([[64,64,64],[128,128,128],[256,256,256]]),
 'epochs': 10
}
 1 139.08439712500012 168711 16.790971167565026 
{
 "learning_rate": tune.uniform(0.001, 1),
 "n_changepoints": 10,
 "n_lags": 3, 
 'drop_missing': True,
 'impute_rolling': 300,
 'newer_samples_weight': tune.uniform(1, 7),
 'batch_size': 128,
 "ar_layers": tune.choice([[64,64,64],[128,128,128],[256,256,256]]),
 'epochs': 10
}

duration of execution:  147.90069438499995


We now see full utlization of the cluster
<br></br>
<div style="text-align: center; line-height: 5; padding-top: 20px;  padding-bottom: 20px;">
  <img src="https://raw.githubusercontent.com/puneet-jain159/Image_dump/test/ray_100_dash_utlization_max.png" alt='Push compute' height="1000" width="1600">
</div>